In [1]:
import pandas as pd
import pymongo
from ydata_profiling import ProfileReport
from autogluon.tabular import TabularDataset, TabularPredictor

In [2]:
config = {
    'mongo_uri': "mongo_uri"
}

In [4]:
client = pymongo.MongoClient(config['mongo_uri'])
db = client.myLOLDB
collection = db['matchups']
# Send a ping to confirm a successful connection
try:
    client.admin.command('ping')
    print("Pinged your deployment. You successfully connected to MongoDB!")
except Exception as e:
    print(e)

Pinged your deployment. You successfully connected to MongoDB!


In [5]:
data_list = []
for matchup in collection.find():
    try:
        for champ in matchup['data']:
            data = {
                'p_match_id': matchup['p_match_id'],
                'gameVersion': matchup['gameVersion']
            }
            data.update(champ)
            data_list.append(data)
    except:
        print("Error in matchup: ", matchup['p_match_id'])

df = pd.DataFrame(data_list)

In [6]:
df.head(5)

p_match_id     gameVersion championName  goldEarned  \
0     BR1_2938902060_TOP  14.10.585.8823      Chogath       12079   
1     BR1_2938902060_TOP  14.10.585.8823     Renekton        9864   
2  BR1_2938902060_JUNGLE  14.10.585.8823      Kindred       11568   
3  BR1_2938902060_JUNGLE  14.10.585.8823        Viego       10727   
4  BR1_2938902060_MIDDLE  14.10.585.8823          Zoe       10316   

   totalMinionsKilled    win  kills  assists  deaths  visionScore  \
0                 187   True      6        9       1           24   
1                 196  False      1        2       6           10   
2                  38   True      2       12       8           37   
3                  18  False      6        7       8           31   
4                 178   True      3        9       3           32   

                                               puuid  \
0  TbhdO_S4OTL11L0W4CaSh68ZT4IfkWM7_R7b-zoguAJUFt...   
1  vghDeb9wbhnQOuqq9F6m3E8JaLgLRX6PVoXT78MWTko8My...   
2  Nke55BF7v4tiMhekVz_D_UjrQsiOUYnhLuDaDGXRqc-JUG...   
3  e3QySsEvF36OgKyz_XuFECc55y8wJXC6cJV98wYXC-KtW0...   
4  _0s-ftcpkX-zV6h4vMc-VGD_4zOYjQQqfGCPpabXj8xohW...   

   totalDamageDealtToChampions     summonerName  
0                        16792           xConan  
1                        11978  our last moment  
2                        14597       COELHOSHOW  
3                        13969           Canyon  
4                        21331        O KOALA 3

In [7]:
report = ProfileReport(df, title='Matchup Exploration', html={'style':{'full_width':True}})

report.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [8]:
df.columns

Index(['p_match_id', 'gameVersion', 'championName', 'goldEarned',
       'totalMinionsKilled', 'win', 'kills', 'assists', 'deaths',
       'visionScore', 'puuid', 'totalDamageDealtToChampions', 'summonerName'],
      dtype='object')

In [9]:
df.drop(columns=['p_match_id', 'gameVersion', 'summonerName', 'gameVersion'], inplace=True)

In [10]:
df.head(5)

championName  goldEarned  totalMinionsKilled    win  kills  assists  deaths  \
0      Chogath       12079                 187   True      6        9       1   
1     Renekton        9864                 196  False      1        2       6   
2      Kindred       11568                  38   True      2       12       8   
3        Viego       10727                  18  False      6        7       8   
4          Zoe       10316                 178   True      3        9       3   

   visionScore                                              puuid  \
0           24  TbhdO_S4OTL11L0W4CaSh68ZT4IfkWM7_R7b-zoguAJUFt...   
1           10  vghDeb9wbhnQOuqq9F6m3E8JaLgLRX6PVoXT78MWTko8My...   
2           37  Nke55BF7v4tiMhekVz_D_UjrQsiOUYnhLuDaDGXRqc-JUG...   
3           31  e3QySsEvF36OgKyz_XuFECc55y8wJXC6cJV98wYXC-KtW0...   
4           32  _0s-ftcpkX-zV6h4vMc-VGD_4zOYjQQqfGCPpabXj8xohW...   

   totalDamageDealtToChampions  
0                        16792  
1                        11978  
2                        14597  
3                        13969  
4                        21331

In [11]:
train = df.sample(frac=0.8, random_state=200)
test = df.drop(train.index)

In [12]:
df = TabularDataset(df)

In [14]:
label = 'win'
predictor = TabularPredictor(label=label, path='./autogluon_trained_model_classifier').fit(train, time_limit=3600)

No presets specified! To achieve strong results with AutoGluon, it is recommended to use the available presets.
	Recommended Presets (For more details refer to https://auto.gluon.ai/stable/tutorials/tabular/tabular-essentials.html#presets):
	presets='best_quality'   : Maximize accuracy. Default time_limit=3600.
	presets='high_quality'   : Strong accuracy with fast inference speed. Default time_limit=3600.
	presets='good_quality'   : Good accuracy with very fast inference speed. Default time_limit=3600.
	presets='medium_quality' : Fast training time, ideal for initial prototyping.
Beginning AutoGluon training ... Time limit = 3600s
AutoGluon will save models to "./autogluon_trained_model_classifier"
=================== System Info ===================
AutoGluon Version:  1.1.0
Python Version:     3.11.5
Operating System:   Windows
Platform Machine:   AMD64
Platform Version:   10.0.22631
CPU Count:          12
Memory Avail:       2.96 GB / 15.34 GB (19.3%)
Disk Space Avail:   56.40 GB / 2

In [16]:
predictor.leaderboard(test)

model  score_test  score_val eval_metric  pred_time_test  \
0   WeightedEnsemble_L2    0.835522     0.8364    accuracy        0.591823   
1              CatBoost    0.834584     0.8312    accuracy        0.046263   
2               XGBoost    0.832864     0.8316    accuracy        0.088297   
3            LightGBMXT    0.829268     0.8280    accuracy        0.025473   
4         LightGBMLarge    0.829112     0.8284    accuracy        0.050340   
5              LightGBM    0.827861     0.8252    accuracy        0.033182   
6      RandomForestGini    0.825516     0.8236    accuracy        0.288883   
7      RandomForestEntr    0.825516     0.8228    accuracy        0.335236   
8        ExtraTreesGini    0.825516     0.8148    accuracy        0.590638   
9        ExtraTreesEntr    0.822233     0.8148    accuracy        0.466898   
10       KNeighborsUnif    0.617886     0.6028    accuracy        0.033633   
11       KNeighborsDist    0.613196     0.5956    accuracy        0.030484   

    pred_time_val   fit_time  pred_time_test_marginal  pred_time_val_marginal  \
0        0.190349  45.845149                 0.013032                0.000000   
1        0.016410  35.495135                 0.046263                0.016410   
2        0.018037   1.664401                 0.088297                0.018037   
3        0.008922   2.282503                 0.025473                0.008922   
4        0.020057   1.888234                 0.050340                0.020057   
5        0.010851   0.879187                 0.033182                0.010851   
6        0.097942   2.377856                 0.288883                0.097942   
7        0.116071   3.485691                 0.335236                0.116071   
8        0.124791   1.943416                 0.590638                0.124791   
9        0.111324   1.799034                 0.466898                0.111324   
10       0.010931   1.078216                 0.033633                0.010931   
11       0.011791   0.033007                 0.030484                0.011791   

    fit_time_marginal  stack_level  can_infer  fit_order  
0            0.149998            2       True         12  
1           35.495135            1       True          7  
2            1.664401            1       True         10  
3            2.282503            1       True          3  
4            1.888234            1       True         11  
5            0.879187            1       True          4  
6            2.377856            1       True          5  
7            3.485691            1       True          6  
8            1.943416            1       True          8  
9            1.799034            1       True          9  
10           1.078216            1       True          1  
11           0.033007            1       True          2

In [18]:
predictor.predict(test)

3        False
4         True
5        False
17        True
18       False
         ...  
31943     True
31949    False
31953     True
31965     True
31970    False
Name: win, Length: 6396, dtype: bool

In [20]:
print(predictor.predict_proba(test).iloc[0])

False    0.912121
True     0.087879
Name: 3, dtype: float64


In [25]:
# Specify the path to the saved model
model_path = 'autogluon_trained_model_classifier'

# Load the tabular predictor
predictor = TabularPredictor.load(model_path)

In [3]:
import requests

def get_my_history():
    url = 'https://sea.api.riotgames.com/lol/match/v5/matches/by-puuid/OKXdwLkxzYKjFgG6df2wrYPsg7B2zzmrksLwC1ZdYWjAh4zSKqj0YWNPxTvurE8NLjHjCkwXi6fywA/ids?type=ranked&start=0&count=20&api_key=RGAPI-5f880b72-69d4-4442-8419-b3352d94f2a8'
    return list(requests.get(url).json())
history_ids = get_my_history()

In [27]:
def get_matches(match_id):
    url = f'https://sea.api.riotgames.com/lol/match/v5/matches/{match_id}?api_key=RGAPI-5f880b72-69d4-4442-8419-b3352d94f2a8'
    for player in requests.get(url).json()['info']['participants']:
        if player['puuid'] == 'OKXdwLkxzYKjFgG6df2wrYPsg7B2zzmrksLwC1ZdYWjAh4zSKqj0YWNPxTvurE8NLjHjCkwXi6fywA':
            return {
                'p_match_id': match_id + '_' + player['teamPosition'],
                'championName': player['championName'],
                'goldEarned': player['goldEarned'],
                'totalMinionsKilled': player['totalMinionsKilled'],
                'win': player['win'],
                'kills': player['kills'],
                "assists": player['assists'],
                "deaths": player['deaths'],
                "visionScore": player['visionScore'],
                "puuid": player['puuid'],
                "totalDamageDealtToChampions": player['totalDamageDealtToChampions'],
                }

In [28]:
df = pd.DataFrame([get_matches(match_id) for match_id in history_ids])

In [29]:
mask = df['p_match_id'].apply(lambda x: x.split('_')[-1] != '')
df = df[mask]

In [30]:
df = TabularDataset(df)
predictor.evaluate(df)

{'accuracy': 0.8333333333333334,
 'balanced_accuracy': 0.85,
 'mcc': 0.7135060680126758,
 'roc_auc': 0.8625,
 'f1': 0.8421052631578947,
 'precision': 0.7272727272727273,
 'recall': 1.0}